In [11]:
import plotly.graph_objects as go
import pandas as pd
import plotly.express as px

# Constants for file paths
INTERPOLATED_CSV_PATH = 'RossPumpCurvesPlotValuesInterpolated.csv'
MAIN_CSV_PATH = 'CanadianSWD_2024-09-19_2024-10-19.csv'

# Column definitions
FLOW_COLUMN = 'flow rate'
PRESSURE_COLUMN = 'discharge pressure'
FREQUENCY_FLOAT_COLUMN = 'frequency'
FREQUENCY_INT_COLUMN = 'frequency int'

# Load the data
df_pump_curve = pd.read_csv(INTERPOLATED_CSV_PATH)
df = pd.read_csv(MAIN_CSV_PATH)

# Ensure 'frequency' column is of type integer for proper usage in color mapping
df[FREQUENCY_FLOAT_COLUMN] = df[FREQUENCY_FLOAT_COLUMN].astype(float)
df[FREQUENCY_INT_COLUMN] = df[FREQUENCY_FLOAT_COLUMN].round().astype('Int64')

# Define the color map for visualization
frequencies = range(50, 61)  # Frequencies from 50Hz to 60Hz
colorscale = px.colors.sequential.Turbo
n_colors = len(colorscale)

# Create color map for frequencies
color_map = {
    freq: colorscale[int((freq - min(frequencies)) / (max(frequencies) - min(frequencies)) * (n_colors - 1))]
    for freq in frequencies
}

# Create pump curve plot
fig = go.Figure()

# Plot pump curve lines (interpolated from df_pump_curve)
for column in df_pump_curve.columns:
    if column != 'X' and ('Hz' in column or column in ['BEP', 'Min', 'Max']):
        # Extract frequency from column name and handle cases where frequency is not in color_map
        if 'Hz' in column:
            try:
                frequency = int(column.replace('Hz', ''))
                line_color = color_map.get(frequency, 'gray')  # Default to 'gray' if frequency is not found in color_map
            except ValueError:
                line_color = 'gray'  # Handle unexpected column names gracefully
        else:
            line_color = 'gray'

        # Add the curve to the figure
        fig.add_trace(
            go.Scatter(
                x=df_pump_curve['X'],
                y=df_pump_curve[column],
                mode='lines',
                name=column,
                line=dict(color=line_color, dash='dash' if 'Hz' in column else 'solid'),
                legendgroup=column.split('Hz')[0] if 'Hz' in column else column,
                showlegend=('Hz' not in column or frequency == 50)  # Show legend only for one frequency line for clarity
            )
        )

# Plot actual data points
for freq in df[FREQUENCY_INT_COLUMN].unique():
    if pd.notna(freq):  # Handle potential NaN values
        freq_data = df[df[FREQUENCY_INT_COLUMN] == freq]
        fig.add_trace(
            go.Scatter(
                x=freq_data[FLOW_COLUMN],
                y=freq_data[PRESSURE_COLUMN],
                mode='markers',
                name=f'{freq}Hz Data',
                marker=dict(color=color_map.get(freq, 'black')),  # Use a default color if the frequency is not in the color_map
                legendgroup=f'{freq}Hz',
                showlegend=True
            )
        )

# Customize plot layout
fig.update_layout(
    title='Pump Curve Visualization',
    xaxis_title='Flow Rate (BBL/day)',
    yaxis_title='Discharge Pressure (PSI)',
    template='plotly_white',
    height=600,
    width=1000,
    legend=dict(title="Legend", orientation="h", x=0, y=-0.2)  # Move legend below the plot to declutter
)

# Show the figure
fig.show()


In [13]:
import os
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.express as px
from shapely.geometry import LineString, Point
from shapely.ops import nearest_points

# Step 1: Load the pickle file
# Replace 'YOUR_FILE_PATH_HERE.pkl' with the path to your pickle file
file_path = '/content/CanadianSWD_2023-11-20_2024-11-14.pkl'
df = pd.read_pickle(file_path)

# Ensure 'timestamp' is parsed as datetime and set as index
if 'timestamp' in df.columns:
    df['timestamp'] = pd.to_datetime(df['timestamp'])
    df.set_index('timestamp', inplace=True)
else:
    print("Timestamp column not found. Please verify your dataset.")

# Step 2: Apply filtering and data preparation
start_date = '2024-10-10'
end_date = df.index.max()
date_filter = (start_date, end_date)
df = df.loc[start_date:end_date]

# Define pump-related variables
pressure_column = 'discharge pressure'
flow_column = 'flow rate'
frequency_float_column = 'frequency'
frequency_int_column = 'frequency int'

# Apply filtering masks on the main DataFrame (df)
# Filter for frequencies between 40 and 60, flow rate > 5000, and discharge pressure > 1300
mask = (40 <= df[frequency_float_column].astype(float)) & (df[frequency_float_column].astype(float) <= 60)
mask &= df[flow_column].astype(float) > 5000
mask &= df[flow_column].astype(float) < 30000
mask &= df[pressure_column].astype(float) > 1300
df = df[mask]

# Round the 'frequency' column
df[frequency_int_column] = df[frequency_float_column].round().astype('Int64')

# Step 3: Create 'watts' column and 'cost_by_flow' column
df['watts'] = df['amps'] * df['volts']

# Avoid division by zero by replacing zeros with NaN in 'watts'
df['watts'].replace(0, np.nan, inplace=True)

# Calculate the cost by flow
df['cost_by_flow'] = df['watts'] / df[flow_column]
df.replace([np.inf, -np.inf], np.nan, inplace=True)

# Drop rows with NaN in 'cost_by_flow'
df.dropna(subset=['cost_by_flow'], inplace=True)

# Step 4: Calculate the BEP (Best Efficiency Point) for each frequency as the median flow rate
bep_points = df.groupby(frequency_int_column)[flow_column].median().to_dict()

# Step 5: Calculate percent deviation from BEP for each data point
df['percent_deviation'] = df.apply(
    lambda row: ((row[flow_column] - bep_points.get(row[frequency_int_column], 0)) / (bep_points.get(row[frequency_int_column], 0) + 1e-6)) * 100,
    axis=1
)

# Step 6: Initialize lists to store distance components
distances_x = []
distances_y = []

# Assuming we have 'df_pump_curve' loaded that contains the pump curve information
# Create dummy 'df_pump_curve' for demonstration (replace this with actual data)
# df_pump_curve = pd.read_csv('YOUR_PUMP_CURVE_FILE.csv')

# Define functions for intersection and distance calculation
# Function to find the intersection between two LineStrings
def find_intersection(line1, line2):
    intersection = line1.intersection(line2)
    if intersection.geom_type == 'Point':
        return intersection
    else:
        # If the intersection is not a point (e.g., lines overlap), return None
        return None

# Function to calculate distance components between two points
def calculate_distance_components(point1, point2):
    if point2 is None:
        return np.nan, np.nan
    distance_x = point1.x - point2.x
    distance_y = point1.y - point2.y
    return distance_x, distance_y

# Loop over each row in the DataFrame to calculate intersection and distances
for _, row in df.iterrows():
    try:
        flow_rate = row[flow_column]
        tdh = row[pressure_column]
        frequency = int(row[frequency_int_column])

        point = Point(flow_rate, tdh)

        # Create the BEP and frequency lines, ensuring valid data
        if df_pump_curve['X'].notna().any() and df_pump_curve['BEP'].notna().any():
            bep_line = LineString(zip(df_pump_curve['X'], df_pump_curve['BEP']))
        else:
            distances_x.append(np.nan)
            distances_y.append(np.nan)
            continue  # Skip to the next row if invalid data

        if df_pump_curve[f'{frequency}Hz'].notna().all():
            freq_line = LineString(zip(df_pump_curve['X'], df_pump_curve[f'{frequency}Hz']))
        else:
            distances_x.append(np.nan)
            distances_y.append(np.nan)
            continue  # Skip to the next row if invalid data

        # Find the intersection point
        intersection = find_intersection(bep_line, freq_line)

        # Calculate the distance components
        distance_x, distance_y = calculate_distance_components(point, intersection)

        distances_x.append(distance_x)
        distances_y.append(distance_y)

    except Exception as e:
        print(f"Error processing row: {e}")
        distances_x.append(np.nan)
        distances_y.append(np.nan)

# Add distance components to the DataFrame
df['Distance to Intersection X'] = distances_x
df['Distance to Intersection Y'] = distances_y

# Step 7: Plot the results as four vertically stacked Plotly subplots
fig = make_subplots(
    rows=4, cols=1, subplot_titles=(
        "Flow Rate", "Discharge Pressure", "Speed (Frequency)", "Percent Deviation from BEP"),
    shared_xaxes=True,  # Sharing x-axis for better comparison
    vertical_spacing=0.05  # Adjust spacing between subplots
)

# Flow rate subplot
fig.add_trace(go.Scatter(x=df.index, y=df[flow_column], name='Flow Rate'),
              row=1, col=1)

# Discharge pressure subplot
fig.add_trace(go.Scatter(x=df.index, y=df[pressure_column], name='Discharge Pressure'),
              row=2, col=1)

# Speed (Frequency) subplot
fig.add_trace(go.Scatter(x=df.index, y=df[frequency_float_column], name='Speed (Frequency)'),
              row=3, col=1)

# Percent deviation from BEP subplot
fig.add_trace(go.Scatter(x=df.index, y=df['percent_deviation'], name='Percent Deviation from BEP'),
              row=4, col=1)

# Update layout for better readability and interaction
fig.update_layout(height=1200, width=1000, title_text="Pump Performance Analysis - Vertical Stacked Plots", showlegend=True)

# Display the figure
fig.show()


<ipython-input-13-edcc54c90b63>:49: FutureWarning:

A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.



/usr/local/lib/python3.10/dist-packages/shapely/set_operations.py:131: RuntimeWarning:

invalid value encountered in intersection

